In [ ]:
# !git clone https://github.com/simulamet-host/conditional-polyp-diffusion.git
!pip install omegaconf
!pip install pytorch-lightning
!pip install taming-transformers-rom1504
!pip install kornia
!pip install openai-clip


[notice] A new release of pip is available: 24.2 -> 25.2
[notice] To update, run: pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.2
[notice] To update, run: pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.2
[notice] To update, run: pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.2
[notice] To update, run: pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.2
[notice] To update, run: pip install --upgrade pip


In [ ]:
from omegaconf import OmegaConf
import os, sys, datetime, glob, importlib, csv
import random

from einops import rearrange
from PIL import Image

import torch
import numpy as np
torch.serialization.add_safe_globals([np.core.multiarray.scalar, np.dtype])
from torch.utils.data import Dataset
import cv2
import albumentations
import matplotlib.pyplot as plt

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]= "1"
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

csv_path = "../../../04_result/abnormal/P2/mask.txt"

def preprocess_mask(img):
    mask = np.zeros_like(img)
    mask[img >= 150] = 1
    return mask

class SegmentationBase(Dataset):
    def __init__(self, segmentation_root,
                 size=None, random_crop=False, interpolation="bicubic",
                 n_labels=2, shift_segmentation=False):

        self.n_labels = n_labels
        self.shift_segmentation = shift_segmentation
        self.segmentation_root = segmentation_root

        # segmentation_root 경로에 있는 .png 파일 목록을 저장
        self.image_paths = sorted(glob.glob(os.path.join(segmentation_root, "*.png")))
        self._length = len(self.image_paths)

        self.labels = {
            "segmentation_path_": [os.path.join(self.segmentation_root, l)
                                   for l in self.image_paths]
        }
        size = None if size is not None and size <= 0 else size
        self.size = size
        if self.size is not None:
            self.interpolation = interpolation
            self.interpolation = {
                "nearest": cv2.INTER_NEAREST,
                "bilinear": cv2.INTER_LINEAR,
                "bicubic": cv2.INTER_CUBIC,
                "area": cv2.INTER_AREA,
                "lanczos": cv2.INTER_LANCZOS4
            }[self.interpolation]
            self.segmentation_rescaler = albumentations.SmallestMaxSize(max_size=self.size,
                                                                        interpolation=cv2.INTER_NEAREST)
            self.center_crop = not random_crop
            if self.center_crop:
                self.cropper = albumentations.CenterCrop(height=self.size, width=self.size)
            else:
                self.cropper = albumentations.RandomCrop(height=self.size, width=self.size)
            self.preprocessor = self.cropper

    def __len__(self):
        return self._length

    def __getitem__(self, i):
        example = dict((k, self.labels[k][i]) for k in self.labels)
        segmentation = Image.open(example["segmentation_path_"])
        if not segmentation.mode == "L":
            segmentation = segmentation.convert("L")
        assert segmentation.mode == "L", segmentation.mode
        segmentation = np.array(segmentation).astype(np.uint8)

        # Preprocess
        segmentation = preprocess_mask(segmentation)

        if self.shift_segmentation:
            segmentation = segmentation + 1
        if self.size is not None:
            segmentation = self.segmentation_rescaler(image=segmentation)["image"]
        if self.size is not None:
            processed = self.preprocessor(image=segmentation)["image"]
        else:
            processed = segmentation

        onehot = np.eye(self.n_labels)[segmentation]
        example["segmentation"] = onehot
        return example

class MaskSeg(SegmentationBase):
    def __init__(self, size=None, random_crop=False, interpolation='bicubic'):
        super().__init__(
            segmentation_root='../../../04_result/abnormal/P2/mask_sample_sel',  # 생성된 마스크 이미지 폴더로 변경
            size=size,
            random_crop=random_crop,
            interpolation=interpolation,
            n_labels=2
        )

In [ ]:
from scripts.sample_diffusion import load_model
import torch
from torchvision.utils import save_image
from torch.utils.data import DataLoader

def ldm_cond_sample_mask(name, seg, model, index):

    with torch.no_grad():
        seg = rearrange(seg, 'b h w c -> b c h w')
        condition = seg.detach().clone()

        seg = seg.to('cuda').float()
        seg = model.get_learned_conditioning(seg)

        # 각 배치마다 한 장씩 생성
        samples_batch, _ = model.sample_log(cond=seg, batch_size=batch_size, ddim=True,
                                            ddim_steps=200, eta=1.)
        samples_batch = model.decode_first_stage(samples_batch)

        # 생성된 이미지를 저장
        for img in samples_batch:
          save_image((img + 1.0) / 2.0, f'../../../04_result/abnormal/P2/fin_gener/{name}_fake_{index}.png')

        inverted_condition = 1 - condition  # 반전
        save_image(inverted_condition, f'../../../04_result/abnormal/P2/cond_mask/{name}_cond_{index}.png')

In [ ]:
# 수정필요
params = {
    "config_path": "./inf_config.yaml",
    "ckpt_path": "../../../03_model/abnormal/P2/masked_ldm/latent_diffusion-v2.ckpt",

}

# 더미 csv 파일 생성
data_list = os.listdir('../../../01_data/02_preproc/02_abnormal/P2/images') # 수정필요

with open(csv_path, "w") as f:
    for item in data_list:
        f.write(item + "\n")

dataset = MaskSeg(size=512)

In [ ]:
batch_size = 1
config = OmegaConf.load(params["config_path"])
model, _ = load_model(config, params["ckpt_path"], None, None)

Loading model from ../../../03_model/abnormal/masked_ldm/latent_diffusion-v2.ckpt
LatentDiffusion: Running in eps-prediction mode
DiffusionWrapper has 215.23 M params.
Keeping EMAs of 218.
cpu
making attention of type 'vanilla' with 512 in_channels
Working with z of shape (1, 3, 128, 128) = 49152 dimensions.
making attention of type 'vanilla' with 512 in_channels
Restored from ../../../03_model/abnormal/vqvae1/VQVAE-epoch=37.ckpt with 0 missing and 55 unexpected keys


/home/gil/anaconda3/envs/YS_pt/lib/python3.9/site-packages/kornia/feature/lightglue.py:44: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  @torch.cuda.amp.custom_fwd(cast_inputs=torch.float32)


Spatial Rescaler mapping from 2 to 3 channels after resizing.


In [ ]:
num_samples = 20000
num_generated_sampels = 0
dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=True)

while num_generated_sampels < num_samples:
  for x in dataloader:
      if num_generated_sampels >= num_samples:
        break
      seg = x['segmentation']
      ldm_cond_sample_mask("mask", seg, model, num_generated_sampels)
      num_generated_sampels += batch_size

Data shape for DDIM sampling is (1, 3, 128, 128), eta 1.0
Running DDIM Sampling with 200 timesteps


DDIM Sampler: 100%|██████████| 200/200 [00:05<00:00, 37.36it/s]


Data shape for DDIM sampling is (1, 3, 128, 128), eta 1.0
Running DDIM Sampling with 200 timesteps


DDIM Sampler: 100%|██████████| 200/200 [00:05<00:00, 37.40it/s]


Data shape for DDIM sampling is (1, 3, 128, 128), eta 1.0
Running DDIM Sampling with 200 timesteps


...

DDIM Sampler: 100%|██████████| 200/200 [00:05<00:00, 36.20it/s]


Data shape for DDIM sampling is (1, 3, 128, 128), eta 1.0
Running DDIM Sampling with 200 timesteps


DDIM Sampler: 100%|██████████| 200/200 [00:05<00:00, 36.23it/s]


Data shape for DDIM sampling is (1, 3, 128, 128), eta 1.0
Running DDIM Sampling with 200 timesteps


DDIM Sampler: 100%|██████████| 200/200 [00:05<00:00, 36.25it/s]
